In [75]:
# Packages
import numpy as np
import sklearn 
import pandas as pd
import matplotlib.pyplot as plt

from utility_code.utility import utils

In [76]:
#import csvs
train_import = pd.read_csv("ucla2020-cs145-covid19-prediction/train.csv")
test = pd.read_csv("ucla2020-cs145-covid19-prediction/test.csv")
graph = pd.read_csv("ucla2020-cs145-covid19-prediction/graph.csv")

train_import['Norm_Incident'] = train_import['Incident_Rate']/train_import['Testing_Rate']
train_import['Norm_Confirmed'] = train_import['Confirmed']/train_import['Testing_Rate']

In [77]:
#only look at the features in features list
features = ['Confirmed']
num_features = len(features)

train_import

ID  Province_State        Date  Confirmed  Deaths  Recovered  \
0        0         Alabama  04-12-2020       3563      93        NaN   
1        1          Alaska  04-12-2020        272       8       66.0   
2        2         Arizona  04-12-2020       3542     115        NaN   
3        3        Arkansas  04-12-2020       1280      27      367.0   
4        4      California  04-12-2020      22795     640        NaN   
5        5        Colorado  04-12-2020       7307     289        NaN   
6        6     Connecticut  04-12-2020      12035     554        NaN   
7        7        Delaware  04-12-2020       1625      35      191.0   
8        8         Florida  04-12-2020      19895     461        NaN   
9        9         Georgia  04-12-2020      12452     433        NaN   
10      10          Hawaii  04-12-2020        499       9      300.0   
11      11           Idaho  04-12-2020       1407      27        NaN   
12      12        Illinois  04-12-2020      20852     720        NaN   
13      13         Indiana  04-12-2020       7928     343        NaN   
14      14            Iowa  04-12-2020       1587      41      674.0   
15      15          Kansas  04-12-2020       1344      56        NaN   
16      16        Kentucky  04-12-2020       1963      97      464.0   
17      17       Louisiana  04-12-2020      20595     840        NaN   
18      18           Maine  04-12-2020        633      19      266.0   
19      19        Maryland  04-12-2020       8225     236      456.0   
20      20   Massachusetts  04-12-2020      25475     756        NaN   
21      21        Michigan  04-12-2020      24244    1479      433.0   
22      22       Minnesota  04-12-2020       1621      70      842.0   
23      23     Mississippi  04-12-2020       2781      96        NaN   
24      24        Missouri  04-12-2020       4269     118        NaN   
25      25         Montana  04-12-2020        387       6      169.0   
26      26        Nebraska  04-12-2020        791      17        NaN   
27      27          Nevada  04-12-2020       2836     112        NaN   
28      28   New Hampshire  04-12-2020        929      23      236.0   
29      29      New Jersey  04-12-2020      61850    2350        NaN   
30      30      New Mexico  04-12-2020       1245      26      235.0   
31      31        New York  04-12-2020     189033    9385    23887.0   
32      32  North Carolina  04-12-2020       4570      89        NaN   
33      33    North Dakota  04-12-2020        308       7      121.0   
34      34            Ohio  04-12-2020       6604     253        NaN   
35      35        Oklahoma  04-12-2020       1970      96      865.0   
36      36          Oregon  04-12-2020       1527      52        NaN   
37      37    Pennsylvania  04-12-2020      22938     557        NaN   
38      38    Rhode Island  04-12-2020       2665      63       35.0   
39      39  South Carolina  04-12-2020       3320      82        NaN   
40      40    South Dakota  04-12-2020        730       6      197.0   
41      41       Tennessee  04-12-2020       5508     106     1504.0   
42      42           Texas  04-12-2020      13677     283     2014.0   
43      43            Utah  04-12-2020       2303      18        NaN   
44      44         Vermont  04-12-2020        727      27       15.0   
45      45        Virginia  04-12-2020       5274     141        NaN   
46      46      Washington  04-12-2020      10609     506        NaN   
47      47   West Virginia  04-12-2020        593       6       83.0   
48      48       Wisconsin  04-12-2020       3341     144        NaN   
49      49         Wyoming  04-12-2020        270       0      137.0   
50      50         Alabama  04-13-2020       3734      99        NaN   
51      51          Alaska  04-13-2020        277       8       85.0   
52      52         Arizona  04-13-2020       3705     122        NaN   
53      53        Arkansas  04-13-2020       1410      29      391.0   
54      54      California  04-13-2020      2393

In [78]:
#array of states
states = pd.Series.unique(train_import['Province_State'])
num_states = len(states)

In [79]:
#split training into training and testing
# PERCENT_TRAIN = 80
# train , test = utils.split_dataframe(train_import,PERCENT_TRAIN,num_states)

train = train_import

In [80]:
#stratify by state (into state dictionary)
statesdata = {}
for s in states:
    statesdata[s] = train.loc[train['Province_State'] == s ,features]
    
#feature name -> column indices
state_feature_indices = utils.get_column_indices(statesdata['California'],features)

In [81]:
#set the WINDOW size
WINDOW_SIZE = 3

In [82]:
#append the feature spaces from the W days prior (where W is the window length)
all_new_features = []
new_features = []
for day in range(WINDOW_SIZE):
    for f in features:
        new_features.append(f + "(-"+ str(WINDOW_SIZE-day) + " days)")
all_new_features = new_features + features

In [83]:
from itertools import chain

#fill the knn data using days from training set
workingdata = pd.DataFrame(columns = all_new_features)
num_training_days = len(statesdata['California'])

#fill the table
for d in range(WINDOW_SIZE,num_training_days):
    for s in states:
        workingdata_row_index = workingdata.shape[0]
        workingdata_row = utils.flatten_dataframe(statesdata[s],slice(d-WINDOW_SIZE,d+1), state_feature_indices)
        utils.dataframe_append_row(workingdata,workingdata_row,s,d)     

In [84]:
#number of nearest neighbors
#K_NEIGHBORS = 2

#number of days to predict in the future (for now let's predict for entirety of test labels)
NUM_DAYS_INTO_FUTURE = int(test.shape[0] / num_states)
workingdata.iloc[:,workingdata.shape[1]-num_features:]

Confirmed
Alabama (day 3)               4075
Alaska (day 3)                 293
Arizona (day 3)               3964
Arkansas (day 3)              1569
California (day 3)           26686
Colorado (day 3)              7956
Connecticut (day 3)          14755
Delaware (day 3)              2014
Florida (day 3)              22511
Georgia (day 3)              14987
Hawaii (day 3)                 524
Idaho (day 3)                 1473
Illinois (day 3)             24593
Indiana (day 3)               8960
Iowa (day 3)                  1995
Kansas (day 3)                1504
Kentucky (day 3)              2210
Louisiana (day 3)            21951
Maine (day 3)                  770
Maryland (day 3)             10032
Massachusetts (day 3)        29918
Michigan (day 3)             28059
Minnesota (day 3)             1809
Mississippi (day 3)           3360
Missouri (day 3)              4791
Montana (day 3)                404
Nebraska (day 3)               901
Nevada (day 3)                3211
New Hampshire (day 3)         1139
New Jersey (day 3)           71030
New Mexico (day 3)            1484
New York (day 3)            214454
North Carolina (day 3)        5340
North Dakota (day 3)           365
Ohio (day 3)                  7794
Oklahoma (day 3)              2263
Oregon (day 3)                1663
Pennsylvania (day 3)         26753
Rhode Island (day 3)          3251
South Carolina (day 3)        3656
South Dakota (day 3)          1168
Tennessee (day 3)             5827
Texas (day 3)                15907
Utah (day 3)                  2548
Vermont (day 3)                759
Virginia (day 3)              6500
Washington (day 3)           10942
West Virginia (day 3)          702
Wisconsin (day 3)             3721
Wyoming (day 3)                287
Alabama (day 4)               4345
Alaska (day 4)                 300
Arizona (day 4)               4237
Arkansas (day 4)              1620
California (day 4)           27677
Colorado (day 4)              8286
Connecticut (day 4)          15884
Delaware (day 4)              2070
Florida (day 4)              23343
Georgia (day 4)              15669
Hawaii (day 4)                 530
Idaho (day 4)                 1587
Illinois (day 4)             25734
Indiana (day 4)               9542
Iowa (day 4)                  2141
Kansas (day 4)                1615
Kentucky (day 4)              2435
Louisiana (day 4)            22532
Maine (day 4)                  796
Maryland (day 4)             10784
Massachusetts (day 4)        32181
Michigan (day 4)             28809
Minnesota (day 4)             1809
Mississippi (day 4)           3624
Missouri (day 4)              5174
Montana (day 4)                415
Nebraska (day 4)               952
Nevada (day 4)                3214
New Hampshire (day 4)         1139
New Jersey (day 4)           75317
New Mexico (day 4)            1484
New York (day 4)            223691
North Carolina (day 4)        5639
North Dakota (day 4)           393
Ohio (day 4)                  8414
Oklahoma (day 4)              2357
Oregon (day 4)                1736
Pennsylvania (day 4)         28258
Rhode Island (day 4)          3529
South Carolina (day 4)        3931
South Dakota (day 4)          1311
Tennessee (day 4)             6375
Texas (day 4)                16876
Utah (day 4)                  2683
Vermont (day 4)                774
Virginia (day 4)              6889
Washington (day 4)           11057
West Virginia (day 4)          728
Wisconsin (day 4)             3875
Wyoming (day 4)                296
Alabama (day 5)               4571
Alaska (day 5)                 309
Arizona (day 5)               4511
Arkansas (day 5)              1695
California (day 5)           29157
Colorado (day 5)              8691
Connecticut (day 5)          16809
Delaware (day 5)              2317
Florida (day 5)              24759
Georgia (day 5)              17194
Hawaii (day 5)                 541
Idaho (day 5)                 1609
Illinois (day 5)             27578
Indiana (day 5)              10154


In [85]:
from sklearn.ensemble import RandomForestRegressor
rf = RandomForestRegressor(max_depth=5, random_state=0)
#rf.fit(workingdata.iloc[:,:-1 * num_features], workingdata.iloc[:,workingdata.shape[1]-num_features:])

#get rid of previously predicted rows
workingdata = workingdata.iloc[:(num_training_days - WINDOW_SIZE)*num_states,:]

#feature name -> column indices
workingdata_feature_indices = utils.get_column_indices(workingdata,features)

#build table for next NUM_DAYS_INTO_FUTURE entries
for d in range(num_training_days,num_training_days + NUM_DAYS_INTO_FUTURE):
    
    #refit the model after every day
    rf.fit(workingdata.iloc[:,:-1 * num_features], workingdata.iloc[:,workingdata.shape[1]-num_features:])
    
    for s in states:
        #get rows for past WINDOW_SIZE days
        
        row_indicies = slice(workingdata.shape[0] - num_states * WINDOW_SIZE, workingdata.shape[0], num_states)
        rf_row_features = utils.flatten_dataframe(workingdata,row_indicies,slice(-1 * num_features,None,None))
        rf_ret = rf.predict([rf_row_features])[0]
        if(num_features == 1):
            rf_row_features.append(rf_ret)
        else:
            rf_row_features.extend(rf_ret.tolist())
            
        utils.dataframe_append_row(workingdata,rf_row_features,s,d)     

/Users/Aditya/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  from ipykernel import kernelapp as app
/Users/Aditya/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  from ipykernel import kernelapp as app
/Users/Aditya/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  from ipykernel import kernelapp as app
/Users/Aditya/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the 

In [86]:
#analyze labels vs predictions
pd.set_option("display.max_rows", None, "display.max_columns", None)
predictions = workingdata.iloc[(num_training_days - WINDOW_SIZE)*num_states:,-1 * num_features:]
labels = utils.dataframe_copy_rows_and_filter_columns(test,predictions)
errors = predictions.subtract(labels)

In [87]:
errors.divide(labels).mean()

Confirmed   -124260.181862
dtype: float64

In [88]:
# Do the same for deaths
#only look at the features in features list
features = ['Deaths']
num_features = len(features)

#array of states
states = pd.Series.unique(train_import['Province_State'])
num_states = len(states)

#split training into training and testing
# PERCENT_TRAIN = 80
# train , test = utils.split_dataframe(train_import,PERCENT_TRAIN,num_states)

#stratify by state (into state dictionary)
statesdata = {}
for s in states:
    statesdata[s] = train.loc[train['Province_State'] == s ,features]
    
#feature name -> column indices
state_feature_indices = utils.get_column_indices(statesdata['California'],features)

#set the WINDOW size
WINDOW_SIZE = 4

#append the feature spaces from the W days prior (where W is the window length)
all_new_features = []
new_features = []
for day in range(WINDOW_SIZE):
    for f in features:
        new_features.append(f + "(-"+ str(WINDOW_SIZE-day) + " days)")
all_new_features = new_features + features
print(all_new_features)

from itertools import chain

#fill the knn data using days from training set
workingdata = pd.DataFrame(columns = all_new_features)
num_training_days = len(statesdata['California'])

#fill the table
for d in range(WINDOW_SIZE,num_training_days):
    for s in states:
        workingdata_row_index = workingdata.shape[0]
        workingdata_row = utils.flatten_dataframe(statesdata[s],slice(d-WINDOW_SIZE,d+1), state_feature_indices)
        utils.dataframe_append_row(workingdata,workingdata_row,s,d)     

#number of nearest neighbors
#K_NEIGHBORS = 2

#number of days to predict in the future (for now let's predict for entirety of test labels)
NUM_DAYS_INTO_FUTURE = int(test.shape[0] / num_states)
print(workingdata.iloc[:,workingdata.shape[1]-num_features:])

from sklearn.ensemble import RandomForestRegressor
rf = RandomForestRegressor(max_depth=5, random_state=0)
#rf.fit(workingdata.iloc[:,:-1 * num_features], workingdata.iloc[:,workingdata.shape[1]-num_features:])

#get rid of previously predicted rows
workingdata = workingdata.iloc[:(num_training_days - WINDOW_SIZE)*num_states,:]

#feature name -> column indices
workingdata_feature_indices = utils.get_column_indices(workingdata,features)

#build table for next NUM_DAYS_INTO_FUTURE entries
for d in range(num_training_days,num_training_days + NUM_DAYS_INTO_FUTURE):
    
    #refit the model after every day
    rf.fit(workingdata.iloc[:,:-1 * num_features], workingdata.iloc[:,workingdata.shape[1]-num_features:])
    
    for s in states:
        #get rows for past WINDOW_SIZE days
        
        row_indicies = slice(workingdata.shape[0] - num_states * WINDOW_SIZE, workingdata.shape[0], num_states)
        rf_row_features = utils.flatten_dataframe(workingdata,row_indicies,slice(-1 * num_features,None,None))
        rf_ret = rf.predict([rf_row_features])[0]
        if(num_features == 1):
            rf_row_features.append(rf_ret)
        else:
            rf_row_features.extend(rf_ret.tolist())
            
        utils.dataframe_append_row(workingdata,rf_row_features,s,d)     


['Deaths(-4 days)', 'Deaths(-3 days)', 'Deaths(-2 days)', 'Deaths(-1 days)', 'Deaths']
                         Deaths
Alabama (day 4)             133
Alaska (day 4)                9
Arizona (day 4)             150
Arkansas (day 4)             37
California (day 4)          956
Colorado (day 4)            355
Connecticut (day 4)         971
Delaware (day 4)             55
Florida (day 4)             668
Georgia (day 4)             587
Hawaii (day 4)                9
Idaho (day 4)                41
Illinois (day 4)           1072
Indiana (day 4)             477
Iowa (day 4)                 60
Kansas (day 4)               80
Kentucky (day 4)            129
Louisiana (day 4)          1156
Maine (day 4)                27
Maryland (day 4)            319
Massachusetts (day 4)      1108
Michigan (day 4)           1996
Minnesota (day 4)            87
Mississippi (day 4)         129
Missouri (day 4)            169
Montana (day 4)               7
Nebraska (day 4)             21
Nevada (day 4)   

/Users/Aditya/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:68: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
/Users/Aditya/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:68: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
/Users/Aditya/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:68: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
/Users/Aditya/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:68: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
/Users/Aditya/anaconda3/lib/python3.6/site-packages/ipykernel_launch

In [89]:
#analyze labels vs predictions
pd.set_option("display.max_rows", None, "display.max_columns", None)
predictions2 = workingdata.iloc[(num_training_days - WINDOW_SIZE)*num_states:,-1 * num_features:]
labels2 = utils.dataframe_copy_rows_and_filter_columns(test,predictions2)
errors2 = predictions2.subtract(labels2)

In [90]:
errors2.divide(labels2).mean()

Deaths   -3664.861218
dtype: float64

In [91]:
predictions2

Deaths
Alabama (day 142)         2070.05
Alaska (day 142)          82.4752
Arizona (day 142)         4936.19
Arkansas (day 142)        688.347
California (day 142)      12745.2
Colorado (day 142)        2058.76
Connecticut (day 142)      4345.5
Delaware (day 142)        688.347
Florida (day 142)           10753
Georgia (day 142)         5919.77
Hawaii (day 142)          82.4752
Idaho (day 142)           361.588
Illinois (day 142)         8269.7
Indiana (day 142)         3317.85
Iowa (day 142)            1071.01
Kansas (day 142)          364.509
Kentucky (day 142)        1071.01
Louisiana (day 142)       4918.46
Maine (day 142)           82.4752
Maryland (day 142)        3888.92
Massachusetts (day 142)   8896.21
Michigan (day 142)        6697.06
Minnesota (day 142)       2004.82
Mississippi (day 142)     2678.86
Missouri (day 142)        1562.36
Montana (day 142)         82.4752
Nebraska (day 142)        361.588
Nevada (day 142)          1316.58
New Hampshire (day 142)   361.588
New Jersey (day 142)      15817.7
New Mexico (day 142)      688.347
New York (day 142)        32784.9
North Carolina (day 142)  2684.03
North Dakota (day 142)    82.4752
Ohio (day 142)             4167.4
Oklahoma (day 142)        691.991
Oregon (day 142)          364.509
Pennsylvania (day 142)    7684.91
Rhode Island (day 142)    1071.01
South Carolina (day 142)  2695.35
South Dakota (day 142)    82.4752
Tennessee (day 142)       1716.41
Texas (day 142)           12492.3
Utah (day 142)            361.588
Vermont (day 142)         82.4752
Virginia (day 142)        2678.86
Washington (day 142)      2058.76
West Virginia (day 142)   149.462
Wisconsin (day 142)       1071.01
Wyoming (day 142)         82.4752
Alabama (day 143)         2059.68
Alaska (day 143)          82.7887
Arizona (day 143)         4940.76
Arkansas (day 143)        690.363
California (day 143)      12742.1
Colorado (day 143)        2059.68
Connecticut (day 143)     4286.97
Delaware (day 143)        690.363
Florida (day 143)         10758.6
Georgia (day 143)         5976.38
Hawaii (day 143)          82.7887
Idaho (day 143)           362.943
Illinois (day 143)        8547.49
Indiana (day 143)         3339.98
Iowa (day 143)            1073.12
Kansas (day 143)          362.943
Kentucky (day 143)        1073.12
Louisiana (day 143)       4940.76
Maine (day 143)           82.7887
Maryland (day 143)        4099.48
Massachusetts (day 143)   8853.38
Michigan (day 143)        6696.04
Minnesota (day 143)       2059.68
Mississippi (day 143)     2687.24
Missouri (day 143)        1563.44
Montana (day 143)         82.7887
Nebraska (day 143)        362.943
Nevada (day 143)          1374.41
New Hampshire (day 143)   362.943
New Jersey (day 143)      15813.3
New Mexico (day 143)      690.363
New York (day 143)        32784.4
North Carolina (day 143)  2687.24
North Dakota (day 143)    82.7887
Ohio (day 143)            4201.86
Oklahoma (day 143)        690.363
Oregon (day 143)          362.943
Pennsylvania (day 143)    7698.33
Rhode Island (day 143)    1073.12
South Carolina (day 143)  2687.24
South Dakota (day 143)    82.7887
Tennessee (day 143)       1660.02
Texas (day 143)           12503.1
Utah (day 143)            362.943
Vermont (day 143)         82.7887
Virginia (day 143)        2687.24
Washington (day 143)      2059.68
West Virginia (day 143)   82.7887
Wisconsin (day 143)       1073.12
Wyoming (day 143)         82.7887
Alabama (day 144)         2064.71
Alaska (day 144)          82.9581
Arizona (day 144)         4950.04
Arkansas (day 144)        692.357
California (day 144)        12778
Colorado (day 144)        2064.71
Connecticut (day 144)      4274.5
Delaware (day 144)        692.357
Florida (day 144)         10789.9
Georgia (day 144)         6012.59
Hawaii (day 144)          82.9581
Idaho (day 144)           364.038
Illinois (day 144)        8740.09
Indiana (day 144)         3361.16
Iowa (day 144)            1075.97
Kansas (day 144)          364.038
Kentucky (day 144)        1075.97
Louisiana (day 

In [92]:
ret = pd.concat([predictions, predictions2], axis=1)
ret.columns = ['Confirmed', 'Deaths']
ret['ForecastID'] = np.arange(len(ret))
ret = ret[['ForecastID','Confirmed','Deaths']]
ret

ForecastID Confirmed   Deaths
Alabama (day 142)                  0    123387  2070.05
Alaska (day 142)                   1   7941.86  82.4752
Arizona (day 142)                  2    205806  4936.19
Arkansas (day 142)                 3   63908.2  688.347
California (day 142)               4    696814  12745.2
Colorado (day 142)                 5   58488.5  2058.76
Connecticut (day 142)              6   51863.1   4345.5
Delaware (day 142)                 7   15383.8  688.347
Florida (day 142)                  8    620682    10753
Georgia (day 142)                  9    289463  5919.77
Hawaii (day 142)                  10   8060.17  82.4752
Idaho (day 142)                   11     31900  361.588
Illinois (day 142)                12    239145   8269.7
Indiana (day 142)                 13   92153.3  3317.85
Iowa (day 142)                    14   64019.1  1071.01
Kansas (day 142)                  15   41944.4  364.509
Kentucky (day 142)                16     51556  1071.01
Louisiana (day 142)               17    146398  4918.46
Maine (day 142)                   18   2319.21  82.4752
Maryland (day 142)                19    106600  3888.92
Massachusetts (day 142)           20    126080  8896.21
Michigan (day 142)                21    112937  6697.06
Minnesota (day 142)               22   76289.5  2004.82
Mississippi (day 142)             23   85463.3  2678.86
Missouri (day 142)                24   89772.6  1562.36
Montana (day 142)                 25   8060.17  82.4752
Nebraska (day 142)                26   32071.4  361.588
Nevada (day 142)                  27   70693.2  1316.58
New Hampshire (day 142)           28   8060.17  361.588
New Jersey (day 142)              29    192019  15817.7
New Mexico (day 142)              30   23314.4  688.347
New York (day 142)                31    434292  32784.9
North Carolina (day 142)          32    168023  2684.03
North Dakota (day 142)            33   15154.9  82.4752
Ohio (day 142)                    34    123221   4167.4
Oklahoma (day 142)                35   63664.9  691.991
Oregon (day 142)                  36     26049  364.509
Pennsylvania (day 142)            37    141630  7684.91
Rhode Island (day 142)            38   23158.5  1071.01
South Carolina (day 142)          39    122471  2695.35
South Dakota (day 142)            40   15383.8  82.4752
Tennessee (day 142)               41    158261  1716.41
Texas (day 142)                   42    635682  12492.3
Utah (day 142)                    43   51760.9  361.588
Vermont (day 142)                 44   2319.21  82.4752
Virginia (day 142)                45    123221  2678.86
Washington (day 142)              46   76289.5  2058.76
West Virginia (day 142)           47   8060.17  149.462
Wisconsin (day 142)               48   76289.5  1071.01
Wyoming (day 142)                 49   2319.21  82.4752
Alabama (day 143)                 50    123728  2059.68
Alaska (day 143)                  51   8087.51  82.7887
Arizona (day 143)                 52    211176  4940.76
Arkansas (day 143)                53   64238.6  690.363
California (day 143)              54    697336  12742.1
Colorado (day 143)                55     63502  2059.68
Connecticut (day 143)             56     51958  4286.97
Delaware (day 143)                57   15451.8  690.363
Florida (day 143)                 58    621985  10758.6
Georgia (day 143)                 59    296306  5976.38
Hawaii (day 143)                  60   8087.51  82.7887
Idaho (day 143)                   61   32026.5  362.943
Illinois (day 143)                62    241431  8547.49
Indiana (day 143)                 63   90860.7  3339.98
Iowa (day 143)                    64   64238.6  1073.12
Kansas (day 143)                  65   42128.9  362.943
Kentucky (day 143)                66     51958  1073.12
Louisiana (day 143)               67    144419  4940.76
Maine (day 143)                   68   2324.04  82.7887
Maryland (day 143)                69    106995  4099.48
Massachusetts (day 143)           70    123728  88

In [93]:
ret.to_csv('test_submission_Nov23.csv',index = False)

In [ ]:
# not good